In [1]:
import os
import re
import pandas as pd

# Create Initial Dataframe with all video IDs
dataset_folder = "../../video_titles"
data_records = []

# Regex pattern to extract Video Id and Title from the filename
filename_pattern = re.compile(r"^(.*?)\.txt$")

for file in sorted(os.listdir(dataset_folder)): 
    if file.endswith(".txt"):  # Ensure it's a valid transcript file
        match = filename_pattern.match(file)
        video_id = match.group(1)  # Extract Video Id and Title

        with open(os.path.join(dataset_folder, file), 'r', encoding='utf-8') as file:
            video_title = file.read()

            # Append data to the list
            data_records.append({
                "Video Title": video_title,
                "Link": f"https://www.youtube.com/watch?v={video_id}",
                "HLTA Topics":[]
            })

# Convert to DataFrame
topics_per_video_df = pd.DataFrame(data_records)
topics_per_video_df.set_index("Video Title", inplace=True)

topics_per_video_df 

Link  \
Video Title                                                                                       
$200 Luxury Beach Hotel in The Philippines 🇵🇭       https://www.youtube.com/watch?v=--8n6A8Q6M0   
Marine reacts to the Philippine Light Reaction ...  https://www.youtube.com/watch?v=-1B7cVoZr1c   
Ultimate Filipino Food Festival In The Netherla...  https://www.youtube.com/watch?v=-7vF5F-1btE   
SHOWING MY SISTER SB19 'GENTO' Music Video          https://www.youtube.com/watch?v=-9bfDHHneyU   
10 Reasons/Do not Retire TO the Philippines/Mov...  https://www.youtube.com/watch?v=-C5iB25BRsA   
...                                                                                         ...   
PHILIPPINES PROVINCE LIFE IS SO DIFFERENT FROM ...  https://www.youtube.com/watch?v=zm_8N4vFnZw   
Starring real-life gay couple, latest Filipino ...  https://www.youtube.com/watch?v=zpT46etTP6E   
🇰🇷Koreans React to P-pop Idol Group | Lovey Dov...  https://www.youtube.com/watch?v=zqvDHfgxWh8   
FOREIGNER LIVING IN YHE PHILIPPINES  WEEKLY FOO...  https://www.youtube.com/watch?v=zvTP6wl9sTU   
We were sent a SURPRISE BLESSING in the PHILIPP...  https://www.youtube.com/watch?v=zx-bATPSFaM   

                                                   HLTA Topics  
Video Title                                                     
$200 Luxury Beach Hotel in The Philippines 🇵🇭               []  
Marine reacts to the Philippine Light Reaction ...          []  
Ultimate Filipino Food Festival In The Netherla...          []  
SHOWING MY SISTER SB19 'GENTO' Music Video                  []  
10 Reasons/Do not Retire TO the Philippines/Mov...          []  
...                                                        ...  
PHILIPPINES PROVINCE LIFE IS SO DIFFERENT FROM ...          []  
Starring real-life gay couple, latest Filipino ...          []  
🇰🇷Koreans React to P-pop Idol Group | Lovey Dov...          []  
FOREIGNER LIVING IN YHE PHILIPPINES  WEEKLY FOO...          []  
We were sent a SURPRISE BLESSING in the PHILIPP...          []  

[2704 rows x 2 columns]

In [2]:
# Store results as a flat list
import json

nodes_filename = 'T3.nodes.json'
nodes_filepath = '../output-jsons/' + nodes_filename

with open(nodes_filepath, 'r') as f:
    data = json.load(f)

def flatten_tree(node, depth=1, result=[]):
    """Recursively flattens a tree structure into a list."""
    result.append({
        "id": node["id"],
        "texts": node["text"].split(),
        "level": depth
    })
    
    for child in node.get("children", []):
        flatten_tree(child, depth + 1, result)
    
    return result

# Process each root node in the JSON
flat_list = []
for root in data:
    flat_list.extend(flatten_tree(root))

print(flat_list)

[{'id': 'Z41', 'texts': ['mind', 'history', 'language', 'spanish', 'true', 'sense', 'war'], 'level': 1}, {'id': 'Z35', 'texts': ['airport', 'business', 'flight', 'company', 'issue', 'online', 'plane'], 'level': 2}, {'id': 'Z211', 'texts': ['airport', 'flight', 'plane', 'terminal', 'board'], 'level': 3}, {'id': 'Z143', 'texts': ['airport', 'terminal'], 'level': 4}, {'id': 'Z142', 'texts': ['flight', 'plane', 'board'], 'level': 4}, {'id': 'Z210', 'texts': ['business', 'company', 'issue', 'online', 'reason', 'card', 'transportation'], 'level': 3}, {'id': 'Z137', 'texts': ['internet', 'hotel', 'wifus', 'average', 'haircut', 'luke', 'shave'], 'level': 4}, {'id': 'Z141', 'texts': ['transportation', 'public', 'bus'], 'level': 4}, {'id': 'Z134', 'texts': ['business', 'company', 'issue', 'reason', 'deal', 'owner', 'aware'], 'level': 4}, {'id': 'Z140', 'texts': ['phone', 'fee', 'charge', 'app'], 'level': 4}, {'id': 'Z135', 'texts': ['western', 'personal', 'figure', 'standard', 'base', 'mad', 'hu

In [3]:
from collections import defaultdict

topic_map_filepath = '../output-jsons/' + 'T3.topics.json'

with open(topic_map_filepath, 'r') as f:
    topic_mapping_data = json.load(f)

topic_ids_per_vid_mapping = defaultdict(list)

# use dictionary to change mapping to list topics per video
# doc id serves as the grouping key
for topic_obj in topic_mapping_data:
    topic = topic_obj["topic"]
    
    for doc_entry in topic_obj["doc"]:
        doc_number, probability = doc_entry
        topic_ids_per_vid_mapping[doc_number].append((topic, probability))


# Document numbers are based on the order they are fed into the HLTA model or which line they are in orig text file, starts from 0 til n

In [4]:
# link the top words to the video instead of just the topic id
topic_to_words = {entry["id"]: (", ".join(entry["texts"]), entry["level"]) for entry in flat_list}

# store data in a new dictionary
topic_words_per_vid_mapping = defaultdict(list)

for doc, topic_list in topic_ids_per_vid_mapping.items():
    for t, p in topic_list:
        if t in topic_to_words:
            topic_words, level = topic_to_words[t]
            topic_words_per_vid_mapping[doc].append((topic_words, level, p))
        else:
            topic_words_per_vid_mapping[doc].append((t, None, p))  # Handle case where topic ID is not found

for doc, topic_list in topic_words_per_vid_mapping.items():
    topics_str = ", ".join(f"{t} (Level {lvl}): {p:.2f}" if lvl is not None else f"{t}: {p:.2f}" for t, lvl, p in topic_list)
    print(f"Document {doc} - {topics_str}")

Document 936 - manila-manila, mall, bgc, building, metro, makati, modern (Level 3): 1.00, island, road, beach, local, ride, car, taxi (Level 1): 1.00, peso, dollar, cheap, expensive, peso-peso, price, cheaper (Level 3): 0.86, incredible, unbelievable, lake, volcano (Level 4): 0.75, beach, beach-beach (Level 4): 1.00, bgc, modern, global (Level 4): 0.99, road, local, ride, car, taxi, friendly, bike (Level 2): 1.00, mind, history, language, spanish, true, sense, war (Level 1): 1.00, language-language, language (Level 4): 1.00, meal, restaurant, fresh, noodle, mix, soft, soy-sauce (Level 3): 0.51, airport, terminal (Level 4): 1.00, white, green, brown (Level 4): 0.55, market, grocery, sell, supermarket (Level 4): 0.56, mountain, foot, river, blue, sky, bamboo, tree (Level 2): 0.76, yum, chain, item, donut (Level 4): 0.71, instagram, lifestyle, blog, request, tone (Level 4): 0.95, safe, stay, safety, gym, condo (Level 4): 0.84, mind, sense, single, main, woman, conversation, leave (Level 2

In [5]:
# append into main dataframe
for doc, topic_list in topic_words_per_vid_mapping.items():
    # Group topics by level
    level_groups = defaultdict(list)
    for t, lvl, p in topic_list:
        level_groups[lvl].append((t, p))

   
    sorted_levels = sorted(level_groups.keys(), reverse=True, key=lambda x: x if x is not None else -1)

  
    formatted_text = ""
    for i, lvl in enumerate(sorted_levels):
        if lvl is not None:
            formatted_text += f"Level {lvl}\n"
        for t, p in level_groups[lvl]:
            formatted_text += f"{t}: ({p:.2f})\n"
        formatted_text += "\n"  

    
    topics_per_video_df.iloc[int(doc), 1] = formatted_text.strip()  

In [6]:
topics_per_video_df.to_csv("T3-topics-per-vid.csv")